In [8]:
import csv
import numpy as np  # http://www.numpy.org
import ast
from datetime import datetime
from math import log, floor, ceil

Modify the Utility class's methods. You can also add additional methods as required but don't change existing methods' arguments.

In [9]:
class Utility(object):
    
    # This method computes entropy for information gain
    def entropy(self, class_y):
        # Input:            
        #   class_y         : list of class labels (0's and 1's)

        # TODO: Compute the entropy for a list of classes
        #
        # Example:
        #    entropy([0,0,0,1,1,1,1,1,1]) = 0.92

        entropy = 0
        ### Implement your code here
        #############################################
        
        p = np.mean(class_y)
        if p == 0 or p == 1: return 0
        entropy = - p * log(p) - (1 - p) * log(1 - p)
        
        #############################################
        return entropy


    def partition_classes(self, X, y, split_attribute, split_val):
        # Inputs:
        #   X               : data containing all attributes
        #   y               : labels
        #   split_attribute : column index of the attribute to split on
        #   split_val       : a numerical value to divide the split_attribute

 

        # TODO: Partition the data(X) and labels(y) based on the split value - BINARY SPLIT.
        # 
        # Split_val should be a numerical value
        # For example, your split_val could be the mean of the values of split_attribute
        #
        # You can perform the partition in the following way
        # Numeric Split Attribute:
        #   Split the data X into two lists(X_left and X_right) where the first list has all
        #   the rows where the split attribute is less than or equal to the split value, and the 
        #   second list has all the rows where the split attribute is greater than the split 
        #   value. Also create two lists(y_left and y_right) with the corresponding y labels.

 

        '''
        Example:

 

        X = [[3, 10],                 y = [1,
             [1, 22],                      1,
             [2, 28],                      0,
             [5, 32],                      0,
             [4, 32]]                      1]

 

        Here, columns 0 and 1 represent numeric attributes.

 

        Consider the case where we call the function with split_attribute = 0 and split_val = 3 (mean of column 0)
        Then we divide X into two lists - X_left, where column 0 is <= 3  and X_right, where column 0 is > 3.

 

        X_left = [[3, 10],                 y_left = [1,
                  [1, 22],                           1,
                  [2, 28]]                           0]

 

        X_right = [[5, 32],                y_right = [0,
                   [4, 32]]                           1]

 

        ''' 

        X_left = []
        X_right = []

        y_left = []
        y_right = []
        ### Implement your code here
        #############################################
        left = X[:, split_attribute] <= split_val
        right = X[:, split_attribute] > split_val
        X_left = X[left, :] 
        X_right = X[right, :]
        y_left = y[left]
        y_right = y[right]
        
        #############################################
        return (X_left, X_right, y_left, y_right)


    def information_gain(self, previous_y, current_y):
        # Inputs:
        #   previous_y: the distribution of original labels (0's and 1's)
        #   current_y:  the distribution of labels after splitting based on a particular
        #               split attribute and split value

        # TODO: Compute and return the information gain from partitioning the previous_y labels
        # into the current_y labels.
        # You will need to use the entropy function above to compute information gain
        # Reference: http://www.cs.cmu.edu/afs/cs.cmu.edu/academic/class/15381-s06/www/DTs.pdf

        """
        Example:

        previous_y = [0,0,0,1,1,1]
        current_y = [[0,0], [1,1,1,0]]

        info_gain = 0.45915
        """

        info_gain = 0
        ### Implement your code here
        #############################################
        
        p = len(current_y[0]) / len(previous_y)
        if p == 0 or p == 1: return 0
        info_gain = self.entropy(previous_y) - (p * self.entropy(current_y[0]) + (1 - p) * self.entropy(current_y[1]))
        
        #############################################
        return info_gain


    def best_split(self, X, y):
        # Inputs:
        #   X       : Data containing all attributes
        #   y       : labels
        # TODO: For each node find the best split criteria and return the 
        # split attribute, spliting value along with 
        # X_left, X_right, y_left, y_right (using partition_classes)
        '''

        NOTE: Just like taught in class, don't use all the features for a node.
        Repeat the steps:

        1. Select m attributes out of d available attributes
        2. Pick the best variable/split-point among the m attributes
        3. return the split attributes, split point, left and right children nodes data 

        '''
        split_attribute = 0
        split_value = 0
        X_left, X_right, y_left, y_right = [], [], [], []
        ### Implement your code here
        #############################################
        '''
        temp = -1
        for i in range(X.shape[1]):
            SplitVal = np.median(X[:, i])
            X_left, X_right, y_left, y_right = self.partition_classes(X, y, i, SplitVal)
            IG = self.information_gain(y, [y_left, y_right])
            if not np.isnan(IG) and IG > temp:
                temp = IG
                split_attribute = i
        split_value =  np.median(X[:, split_attribute])
        
        '''
        temp = -1
        for i in range(len(X[0])):
            split_attribute = i
            info_gain = -1
            best_split_val = None
            for i in range(len(X)):
                SplitVal = X[i][split_attribute]
                X_left, X_right, y_left, y_right = self.partition_classes(X, y, split_attribute, SplitVal)
                IG = self.information_gain(y, [y_left, y_right])
                if not np.isnan(IG) and IG > info_gain:
                    info_gain = IG
                    best_split_val = SplitVal
            temp_val = best_split_val
            IG = info_gain
            
            if not np.isnan(IG) and IG > temp:
                temp = IG
                split_attribute = i
                split_value = temp_val      
        
        
        
        return split_attribute, split_value, X_left, X_right, y_left, y_right
        #############################################

### Define the classes 'DecisionTree' and 'RandomForest'

Please modify the 'DecisionTree' and 'RandomForest' classes below

In [10]:
class DecisionTree(object):
    def __init__(self, max_depth):
        # Initializing the tree as an empty dictionary or list, as preferred
        #self.tree = np.array([[]])
        self.max_depth = max_depth
        
    	
    def learn(self, X, y, par_node = {}, depth=0):
        # TODO: Train the decision tree (self.tree) using the the sample X and labels y
        # You will have to make use of the functions in Utility class to train the tree

        # Use the function best_split in Utility class to get the best split and 
        # data corresponding to left and right child nodes
        
        # One possible way of implementing the tree:
        #    Each node in self.tree could be in the form of a dictionary:
        #       https://docs.python.org/2/library/stdtypes.html#mapping-types-dict
        #    For example, a non-leaf node with two children can have a 'left' key and  a 
        #    'right' key. You can add more keys which might help in classification
        #    (eg. split attribute and split value)
        ### Implement your code here
        #############################################
        x=Utility()
        '''
        if depth == self.max_depth: y = [stats.mode(y, axis = None)[0]] * len(y)
        if len(y) <= 1:
            self.tree = np.append(self.tree, [["Leaf", np.mean(y, axis = None)[0], np.nan, np.nan]], axis = 1) if len(self.tree[0]) == 0 else np.append(self.tree, [["Leaf", stats.mode(y, axis = None)[0], np.nan, np.nan]], axis = 0)
            
            n = self.tree.shape[0]
            for i in range(n):
                if self.tree[n-1-i, 3] == None:
                    self.tree[n-1-i, 3] = i + 1
        else:
            index, SplitVal,X_left, X_right, y_left, y_right = x.best_split(X, y)
            if len(X_left) == 0 or len(X_right) == 0:
                self.tree = np.append(self.tree, [["Leaf", np.mean(y, axis = None)[0], np.nan, np.nan]], axis = 1) if len(self.tree[0]) == 0 else np.append(self.tree, [["Leaf", stats.mode(y, axis = None)[0], np.nan, np.nan]], axis = 0)
                
                n = self.tree.shape[0]
                for i in range(n):
                    if self.tree[n-1-i, 3] == None:
                        self.tree[n-1-i, 3] = i + 1
            else:
                self.tree = np.append(self.tree, [[index, SplitVal, 1, None]], axis = 1) if len(self.tree[0]) == 0 else np.append(self.tree, [[index, SplitVal, 1, None]], axis = 0)
                self.learn(X_left, y_left, depth + 1)
                self.learn(X_right, y_right, depth + 1)

        '''    
        if len(y) <= 10:
            self.tree = np.append(self.tree, [["Leaf", np.mean(y), np.nan, np.nan]], axis = 0) if hasattr(self, 'tree') else np.array([["Leaf", 1, np.nan, np.nan]])
            n = self.tree.shape[0]
            for i in range(n):
                if self.tree[n-1-i, 3] == None:
                    self.tree[n-1-i, 3] = i + 1
                    
        elif (y == y[0]).all():
            self.tree = np.append(self.tree, [["Leaf", y[0], np.nan, np.nan]], axis = 0) if hasattr(self, 'tree') else np.array([["Leaf", y[0], np.nan, np.nan]])
            n = self.tree.shape[0]
            for i in range(n):
                if self.tree[n-1-i, 3] == None:
                    self.tree[n-1-i, 3] = i + 1
                    
        else:
            index, SplitVal,X_left, X_right, y_left, y_right = x.best_split(X, y)
            if len(X_left) == 0 or len(X_right) == 0:
                self.tree = np.append(self.tree, [["Leaf", np.mean(y), np.nan, np.nan]], axis = 0) if hasattr(self, 'tree') else np.array([["Leaf", np.mean(y), np.nan, np.nan]])
                n = self.tree.shape[0]
                for i in range(n):
                    if self.tree[n-1-i, 3] == None:
                        self.tree[n-1-i, 3] = i + 1
            else:
                self.tree = np.append(self.tree, [[index, SplitVal, 1, None]], axis = 0) if hasattr(self, 'tree') else np.array([[index, SplitVal, 1, None]])
                self.learn(X_left, y_left)
                self.learn(X_right, y_right)
                
      
        #############################################

    def classify(self, record):
        # TODO: classify the record using self.tree and return the predicted label
        ### Implement your code here
        #############################################
        curr = 0
        while True:
            if self.tree[curr, 0] == "Leaf":
                return int(float(self.tree[curr, 1]) + 0.5)
            else:
                curr += self.tree[curr, 2] if record[self.tree[curr, 0]] <= self.tree[curr, 1] else self.tree[curr, 3]

        #############################################

In [11]:
# This starter code does not run. You will have to add your changes and
# turn in code that runs properly.

"""
Here, 
1. X is assumed to be a matrix with n rows and d columns where n is the
number of total records and d is the number of features of each record. 
2. y is assumed to be a vector of labels of length n.
3. XX is similar to X, except that XX also contains the data label for each
record.
"""

"""
This skeleton is provided to help you implement the assignment.You must 
implement the existing functions as necessary. You may add new functions
as long as they are called from within the given classes. 

VERY IMPORTANT!
Do NOT change the signature of the given functions.
Do NOT change any part of the main function APART from the forest_size parameter.  
"""


class RandomForest(object):
    num_trees = 0
    decision_trees = []

    # the bootstrapping datasets for trees
    # bootstraps_datasets is a list of lists, where each list in bootstraps_datasets is a bootstrapped dataset.
    bootstraps_datasets = []

    # the true class labels, corresponding to records in the bootstrapping datasets
    # bootstraps_labels is a list of lists, where the 'i'th list contains the labels corresponding to records in
    # the 'i'th bootstrapped dataset.
    bootstraps_labels = []

    def __init__(self, num_trees):
        # Initialization done here
        self.num_trees = num_trees
        self.decision_trees = [DecisionTree(max_depth=10) for i in range(num_trees)]
        self.bootstraps_datasets = []
        self.bootstraps_labels = []
        
    def _bootstrapping(self, XX, n):
        # Reference: https://en.wikipedia.org/wiki/Bootstrapping_(statistics)
        #
        # TODO: Create a sample dataset of size n by sampling with replacement
        #       from the original dataset XX.
        # Note that you would also need to record the corresponding class labels
        # for the sampled records for training purposes.

        samples = [] # sampled dataset
        labels = []  # class labels for the sampled records
        ### Implement your code here
        #############################################
        
        choice = np.random.randint(0, n, size = n)
        XX = np.array(XX)
        samples = XX[:, :-1][choice]
        labels = XX[:, -1][choice]
        
        #############################################
        return (samples, labels)

    def bootstrapping(self, XX):
        # Initializing the bootstap datasets for each tree
        for i in range(self.num_trees):
            data_sample, data_label = self._bootstrapping(XX, len(XX))
            self.bootstraps_datasets.append(data_sample)
            self.bootstraps_labels.append(data_label)

    def fitting(self):
        # TODO: Train `num_trees` decision trees using the bootstraps datasets
        # and labels by calling the learn function from your DecisionTree class.
        ### Implement your code here
        #############################################
        
        for i in range(self.num_trees):
            self.decision_trees[i].learn(self.bootstraps_datasets[i], self.bootstraps_labels[i])

        #############################################

    def voting(self, X):
        y = []

        for record in X:
            # Following steps have been performed here:
            #   1. Find the set of trees that consider the record as an
            #      out-of-bag sample.
            #   2. Predict the label using each of the above found trees.
            #   3. Use majority vote to find the final label for this recod.
            votes = []
            
            for i in range(len(self.bootstraps_datasets)):
                dataset = self.bootstraps_datasets[i]
                
                if record not in dataset:
                    OOB_tree = self.decision_trees[i]
                    effective_vote = OOB_tree.classify(record)
                    votes.append(effective_vote)

            counts = np.bincount(votes)

            if len(counts) == 0:
                # TODO: Special case
                #  Handle the case where the record is not an out-of-bag sample
                #  for any of the trees.
                # NOTE - you can add few lines of codes above (but inside voting) to make this work
                ### Implement your code here
                #############################################
                
                y = np.append(y, self.decision_trees[0].classify(record))
                
                #############################################
            else:
                y = np.append(y, np.argmax(counts))
                
        return y

    def user(self):
        """
        :return: string
        your GTUsername, NOT your 9-Digit GTId  
        """
        ### Implement your code here
        #############################################
        return 'helfayoumy3'
        #############################################

In [12]:
# TODO: Initialize according to your implementation
# VERY IMPORTANT: Minimum forest_size should be 10
forest_size = 10

### Do not modify the below cell

In [13]:
# start time 
start = datetime.now()
X = list()
y = list()
XX = list()  # Contains data features and data labels
numerical_cols = set([i for i in range(0, 9)])  # indices of numeric attributes (columns)

# Loading data set
print("reading the data")
with open("pima-indians-diabetes.csv") as f:
    next(f, None)
    for line in csv.reader(f, delimiter=","):
        xline = []
        for i in range(len(line)):
            if i in numerical_cols:
                xline.append(ast.literal_eval(line[i]))
            else:
                xline.append(line[i])

        X.append(xline[:-1])
        y.append(xline[-1])
        XX.append(xline[:])

# Initializing a random forest.
randomForest = RandomForest(forest_size)

# printing the name
print("__Name: " + randomForest.user()+"__")

# Creating the bootstrapping datasets
print("creating the bootstrap datasets")
randomForest.bootstrapping(XX)

# Building trees in the forest
print("fitting the forest")
randomForest.fitting()

# Calculating an unbiased error estimation of the random forest
# based on out-of-bag (OOB) error estimate.
y_predicted = randomForest.voting(X)

# Comparing predicted and true labels
results = [prediction == truth for prediction, truth in zip(y_predicted, y)]

# Accuracy
accuracy = float(results.count(True)) / float(len(results))

print("accuracy: %.4f" % accuracy)
print("OOB estimate: %.4f" % (1 - accuracy))

# end time
print("Execution time: " + str(datetime.now() - start))

reading the data
__Name: helfayoumy3__
creating the bootstrap datasets
fitting the forest
accuracy: 0.6519
OOB estimate: 0.3481
Execution time: 0:00:10.655878
